#  MatchPoint: European Football Match & Location Data Pipeline

####MatchPoint is a data-driven decision support tool designed specifically for sports tourists attending international football matches. The system integrates accommodation data from platforms such as Airbnb and Booking.com with externally collected match schedules and stadium geospatial information. Based on a selected match, the system ranks and recommends suitable properties by jointly optimizing three critical variables: property quality, price, and proximity to the stadium. Furthermore, it allows users to adjust the relative importance of these factors, ensuring personalized recommendations that align with individual preferences.

## imports

In [0]:
%pip install python-dotenv
dbutils.library.restartPython()

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
import json
from pyspark.sql import functions as F
from dotenv import load_dotenv  
import os


load_dotenv()

# ==============================================================================
# STEP 1: Load "Submissions" Data (Matches & Stadium JSON)
# ==============================================================================

# 1. Define variables for the First Container
storage_account = "lab94290"
container_submissions = "submissions"
sas_token_submissions = os.getenv('SAS_SUBMISSIONS')
sas_token_submissions = sas_token_submissions.lstrip('?')

# 2. Configure Spark for Submissions
print("🔄 Connecting to 'submissions' container...")
spark.conf.set(f"fs.azure.account.auth.type.{storage_account}.dfs.core.windows.net", "SAS")
spark.conf.set(f"fs.azure.sas.token.provider.type.{storage_account}.dfs.core.windows.net", "org.apache.hadoop.fs.azurebfs.sas.FixedSASTokenProvider")
spark.conf.set(f"fs.azure.sas.fixed.token.{storage_account}.dfs.core.windows.net", sas_token_submissions)

# 3. Define Paths
base_path_submissions = f"abfss://{container_submissions}@{storage_account}.dfs.core.windows.net/Lior_Shachar_Raz/"

# --- Load Matches (DataFrame) ---
matches_df = spark.read.format("csv") \
    .option("header", "true") \
    .option("inferSchema", "true") \
    .load(f"{base_path_submissions}Match_Schedule_All_Leagues.csv")

# --- Load Stadium Guides (Raw JSON Variable) ---
print("📖 Reading 'stadium_guides.json' into local variable...")

# We use Spark to read the file content while the SAS token is valid
json_path = f"{base_path_submissions}stadium_guides.json"
try:
    # wholetext=True reads the entire file into a single row
    json_content_str = spark.read.option("wholetext", "true").text(json_path).collect()[0][0]
    
    # Parse the string into a standard Python JSON object (dict or list)
    stadium_guides_json = json.loads(json_content_str)
    print("✅ 'stadium_guides_json' successfully loaded into memory.")
except Exception as e:
    print(f"❌ Error loading JSON: {e}")
    stadium_guides_json = {}

# 4. Apply Transformations to Matches
matches_df = matches_df.withColumn(
    "match_id",
    F.concat_ws(
        "_",
        F.lower(F.col("home_team")),
        F.lower(F.col("away_team")),
        F.col("Date")
    )
)

# 5. CRITICAL: Cache Matches into RAM
print("⏳ Caching Match data into RAM...")
matches_df = matches_df.cache()

# Trigger action
print(f"   - Matches loaded: {matches_df.count()} rows")

print("Match Schedule:")
display(matches_df.limit(5))

# Optional: Print the first key/item of the JSON to verify
print("Stadium Guides Preview (First Item/Key):")
# If it's a list, print first item; if dict, print keys
if isinstance(stadium_guides_json, list) and len(stadium_guides_json) > 0:
    print(stadium_guides_json[0])
elif isinstance(stadium_guides_json, dict):
    print(list(stadium_guides_json.keys())[:5])


# ==============================================================================
# STEP 2: Load "Airbnb" Data
# ==============================================================================

# 1. Define variables for the Second Container
container_airbnb = "airbnb"
sas_token_airbnb = os.getenv('SAS_AIRBNB')
sas_token_airbnb = sas_token_airbnb.lstrip('?')

# 2. Re-Configure Spark for Airbnb (Overwrites the previous token)
print("🔄 Switching to 'airbnb' container...")
spark.conf.set(f"fs.azure.sas.fixed.token.{storage_account}.dfs.core.windows.net", sas_token_airbnb)

# 3. Load Airbnb Data
path_airbnb = f"abfss://{container_airbnb}@{storage_account}.dfs.core.windows.net/airbnb_1_12_parquet"

airbnb_df = spark.read.parquet(path_airbnb)

# 4. Display to verify
display(airbnb_df.limit(5))

print("✅ All data loaded successfully from both containers!")

🔄 Connecting to 'submissions' container...
📖 Reading 'stadium_guides.json' into local variable...
✅ 'stadium_guides_json' successfully loaded into memory.
⏳ Caching Match data into RAM...
   - Matches loaded: 10172 rows
Match Schedule:


Date Time Country home_team away_team league_name stadium_name latitude longitude match_id 2023-08-04 19:45 Belgium Standard St. Gilloise Belgian Pro League Stade Maurice Dufrasne 50.61 5.54333 standard_st. gilloise_2023-08-04 2023-08-05 12:00 Germany Holstein Kiel Greuther Furth 2. Bundesliga Holstein-Stadion 54.34917 10.12361 holstein kiel_greuther furth_2023-08-05 2023-08-05 12:00 Germany St Pauli Fortuna Dusseldorf 2. Bundesliga Millerntor-Stadion 53.554583 9.967667 st pauli_fortuna dusseldorf_2023-08-05 2023-08-05 14:00 France St Etienne Grenoble Ligue 2 Stade Geoffroy Guichard 45.46083 4.39028 st etienne_grenoble_2023-08-05 2023-08-05 15:00 England Bristol City Preston Championship King Power Stadium 52.620277777778 -1.1422222222222 bristol city_preston_2023-08-05

Stadium Guides Preview (First Item/Key):
['Emirates Stadium', 'Villa Park', 'Dean Court', 'Brentford Community Stadium', 'Falmer Stadium']
🔄 Switching to 'airbnb' container...


name price image description category availability discount reviews ratings seller_info breadcrumbs location lat long guests pets_allowed description_items category_rating house_rules details highlights arrangement_details amenities images available_dates url final_url listing_title property_id listing_name location_details description_by_sections description_html location_details_html is_supperhost host_number_of_reviews host_rating hosts_year host_response_rate is_guest_favorite travel_details pricing_details total_price currency cancellation_policy property_number_of_reviews country postcode_map_url host_image host_details Rental unit in Broadbeach · ★4.96 · 2 bedrooms · 2 beds · 1 bath 238 https://a0.muscache.com/pictures/50ddeaed-5302-4d0c-8200-163b2cddd071.jpg Our exceptionally stylish two bedroom, one bathroom LUXURY holiday apartment is located in the ORACLE T2, right in the heart of beautiful Broadbeach! Every corner of this gorgeous apartment overflows with style, luxury and thoughtful touches. Relax on the ocean facing balcony located directly above the manicured garden terrace and take in the relaxing views and sea breezes. This property is all class and guaranteed to satisfy even the fussiest Airbnb guest!The spaceThe photos speak for themselves. They are a true, accurate and up to date representation of our immaculately presented, squeaky clean, apartment. The furnishings are practical and comfortable and the linen and bedding are soft and luxurious. The master king bedroom opens out onto the large balcony. The second bedroom is a small internal room with a comfortable high quality queen sized bed. The second bedroom does not have a window. Each bedroom has an internal sliding door which provides access to the two way bathroom. Our apartment has been styled with a relaxing holiday in mind.Guest accessPoolSpaGymSauna and steam roomBBQ and entertaining areasGardensSecure off street parking for ONE vehicleAccess to facilities is not guaranteed and may be interrupted by routine and unexpected maintenance schedules.Other things to noteThis property accommodates up to FOUR people only. Children aged two and older are included in the four people rule. No exceptions. Infants UNDER the age of two are very welcome at our place and may stay at no additional charge however we do not provide linen or bedding. Let us know if you would like the link to a local business who hires out baby equipment (travel cots, strollers, high chairs).CHECK IN Available between 3pm and 9pm.Self check in is NOT available at this property. After hours check ins are NOT available. A 3pm check in is not guaranteed and depends on cleaning schedules. CHECK IN APPOINTMENTOur lovely host welcomes you in person on arrival. The booking guest is required to make contact with us via the booking message thread prior to their arrival day to arrange a check in time. A host will not be onsite to meet you unless you have scheduled a check in time. We always do our best to fit in with your travel schedule. IMPORTANTKeys and security fobs will only be issued to the person who made the booking. ID will be required. This is not negotiable. Please read the HOUSE RULES and CANCELLATION POLICY prior to booking our place. We recommend taking out travel insurance to cover any losses which may occur if you need to cancel your booking for an unforeseen reason. NO SMOKING - smoking is NOT permitted anywhere at this complex.CHECK IN / CHECK OUT - NOT AVAILABLE* Christmas Day* New Years Day * Easter SundayEARLY CHECK IN - We will always accommodate an early check in if our place is available. CHECK OUT by 11am - Late check outs are not available and hold up our cleaning team. WHAT WE INCLUDE IN OUR STARTER PACKOur starter pack is designed to help get you started on your holiday and may not last the entire trip. If you are with us for more than two nights, you may need to re stock items at the local supermarket. Woolworths supermarket is located right next door for any additi

✅ All data loaded successfully from both containers!


Find relevant dates for scraping (run once):

Earliest Date: 2022-12-21

Latest Date: 2026-07-31

In [0]:
# from pyspark.sql.functions import col, explode, min, max, split, regexp_replace

# # 1. Clean the string representation of lists and split into an array
# #    Format is like "['2025-01-01', '2025-01-02']" -> remove brackets and quotes
# dates_df = airbnb_df.withColumn(
#     "clean_dates", 
#     split(regexp_replace(col("available_dates"), "[\\[\\]'\" ]", ""), ",")
# )

# # 2. Explode the array so each date gets its own row
# exploded_dates = dates_df.select(explode(col("clean_dates")).alias("date_str"))

# # 3. Filter out empty strings if any
# exploded_dates = exploded_dates.filter(col("date_str") != "")

# # 4. Compute Min and Max directly on the cluster
# result = exploded_dates.agg(
#     min("date_str").alias("earliest_date"), 
#     max("date_str").alias("latest_date")
# ).collect()

# # 5. Print the tiny result
# print(f"Earliest Date: {result[0]['earliest_date']}")
# print(f"Latest Date: {result[0]['latest_date']}")

Earliest Date: 2022-12-21
Latest Date: 2026-07-31


Below is a Value-for-Money (VFM) score integrates all components:
VFM = quality_score × price_score × superhost_factor.

The metric integrates multiple dimensions of  ratings, reviews, host reliability, amenities' scope, cancellation policies, and price per guest. Each component was engineered, normalized, and weighted to reflect its real-world influence on perceived value for guests. 

#### Price Score Calculation

In [0]:
from pyspark.sql.functions import col, when, lit, count 

# We will want currency uniformity ==> USD
airbnb_df.groupBy("currency").count().show() 
airbnb_df = airbnb_df.fillna({"currency": "USD"})
airbnb_df = airbnb_df.filter(col("currency") == "USD") 

# To check if 'discount' attribute is relevant for us.
airbnb_df.select(count(col("discount")).alias("discount_non_null")).show() 


# ============================================================
# 1. Filter out listings with missing or zero price
# ============================================================
airbnb_df = airbnb_df.filter(
    col("total_price").isNotNull() & (col("total_price") != 0) 
)

# ============================================================
# 2. Cast "guests" to integer
#    We create an integer version of the guests column. 
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "guests_int",
    col("guests").cast("int")
)

# ============================================================
# 3. Compute median number of guests (over non-null rows)
#    This is used as a fallback for missing/invalid guest counts.
# ============================================================
median_guests = airbnb_df.approxQuantile("guests_int", [0.5], 0.05)[0]

# ============================================================
# 4. Define a safe guests column:
#    - If guests_int is NULL or <= 0 → use median_guests
#    - Otherwise use guests_int as is 
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "guests_safe",
    when(col("guests_int").isNull() | (col("guests_int") <= 0), int(median_guests))
    .otherwise(col("guests_int")) 
)

# ============================================================
# 5. Compute price per guest
#    Here we use the *nightly* price.
#    If you prefer total trip price, replace "price" with "total_price".
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "price_per_guest",
    (col("total_price") / col("guests_safe")).cast("double")
)

# ============================================================
# 6. Robust normalization of price_per_guest using quantiles
#    Instead of min–max over all data (which is very sensitive to outliers),
#    we use the 5th and 95th percentiles as effective bounds.
# ============================================================

# Compute 5th and 95th percentiles
ppg_low, ppg_high = airbnb_df.approxQuantile(
    "price_per_guest",
    [0.05, 0.95],
    0.01
)

# Protect against degenerate case
if ppg_high == ppg_low:
    ppg_high = ppg_low + 1.0

# Clip price_per_guest to [ppg_low, ppg_high]
airbnb_df = airbnb_df.withColumn(
    "price_per_guest_clipped",
    when(col("price_per_guest") < ppg_low, ppg_low)
    .when(col("price_per_guest") > ppg_high, ppg_high)
    .otherwise(col("price_per_guest"))
)

# Normalize clipped price_per_guest to [0, 1]
ppg_range = ppg_high - ppg_low

airbnb_df = airbnb_df.withColumn(
    "price_per_guest_norm",
    (col("price_per_guest_clipped") - lit(ppg_low)) / lit(ppg_range)
)

# Clamp to [0, 1] to avoid edge cases
airbnb_df = airbnb_df.withColumn(
    "price_per_guest_norm",
    when(col("price_per_guest_norm") < 0, 0.0)
    .when(col("price_per_guest_norm") > 1, 1.0)
    .otherwise(col("price_per_guest_norm"))
)

# ============================================================
# 7. Convert to "price_score":
#    - Cheaper per guest → score close to 1
#    - More expensive per guest → score close to 0
#    Here we use a mild non-linearity (**1.1) to slightly punish
#    expensive listings more strongly.
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "price_score",
    (1.0 - col("price_per_guest_norm")) ** 1.1 
)

display(airbnb_df) 

+--------+-------+
|currency|  count|
+--------+-------+
|    NULL|  34507|
|     USD|2063756|
|     EUR|    617|
+--------+-------+

+-----------------+
|discount_non_null|
+-----------------+
|                0|
+-----------------+



name price image description category availability discount reviews ratings seller_info breadcrumbs location lat long guests pets_allowed description_items category_rating house_rules details highlights arrangement_details amenities images available_dates url final_url listing_title property_id listing_name location_details description_by_sections description_html location_details_html is_supperhost host_number_of_reviews host_rating hosts_year host_response_rate is_guest_favorite travel_details pricing_details total_price currency cancellation_policy property_number_of_reviews country postcode_map_url host_image host_details guests_int guests_safe price_per_guest price_per_guest_clipped price_per_guest_norm price_score Rental unit in Broadbeach · ★4.96 · 2 bedrooms · 2 beds · 1 bath 238 https://a0.muscache.com/pictures/50ddeaed-5302-4d0c-8200-163b2cddd071.jpg Our exceptionally stylish two bedroom, one bathroom LUXURY holiday apartment is located in the ORACLE T2, right in the heart of beautiful Broadbeach! Every corner of this gorgeous apartment overflows with style, luxury and thoughtful touches. Relax on the ocean facing balcony located directly above the manicured garden terrace and take in the relaxing views and sea breezes. This property is all class and guaranteed to satisfy even the fussiest Airbnb guest!The spaceThe photos speak for themselves. They are a true, accurate and up to date representation of our immaculately presented, squeaky clean, apartment. The furnishings are practical and comfortable and the linen and bedding are soft and luxurious. The master king bedroom opens out onto the large balcony. The second bedroom is a small internal room with a comfortable high quality queen sized bed. The second bedroom does not have a window. Each bedroom has an internal sliding door which provides access to the two way bathroom. Our apartment has been styled with a relaxing holiday in mind.Guest accessPoolSpaGymSauna and steam roomBBQ and entertaining areasGardensSecure off street parking for ONE vehicleAccess to facilities is not guaranteed and may be interrupted by routine and unexpected maintenance schedules.Other things to noteThis property accommodates up to FOUR people only. Children aged two and older are included in the four people rule. No exceptions. Infants UNDER the age of two are very welcome at our place and may stay at no additional charge however we do not provide linen or bedding. Let us know if you would like the link to a local business who hires out baby equipment (travel cots, strollers, high chairs).CHECK IN Available between 3pm and 9pm.Self check in is NOT available at this property. After hours check ins are NOT available. A 3pm check in is not guaranteed and depends on cleaning schedules. CHECK IN APPOINTMENTOur lovely host welcomes you in person on arrival. The booking guest is required to make contact with us via the booking message thread prior to their arrival day to arrange a check in time. A host will not be onsite to meet you unless you have scheduled a check in time. We always do our best to fit in with your travel schedule. IMPORTANTKeys and security fobs will only be issued to the person who made the booking. ID will be required. This is not negotiable. Please read the HOUSE RULES and CANCELLATION POLICY prior to booking our place. We recommend taking out travel insurance to cover any losses which may occur if you need to cancel your booking for an unforeseen reason. NO SMOKING - smoking is NOT permitted anywhere at this complex.CHECK IN / CHECK OUT - NOT AVAILABLE* Christmas Day* New Years Day * Easter SundayEARLY CHECK IN - We will always accommodate an early check in if our place is available. CHECK OUT by 11am - Late check outs are not available and hold up our cleaning team. WHAT WE INCLUDE IN OUR STARTER PACKOur starter pack is designed to help get you started on your holiday and may not last the entire trip. If you are with us for more than two nights, you may need to re stock 

#### Property Ratings & Reviews Distribution Detection

In [0]:
# Distribution Detection

airbnb_df.select("ratings").describe().show()
airbnb_df.select("property_number_of_reviews").describe().show()

airbnb_df.groupBy("ratings").count().orderBy("ratings").show()
airbnb_df.groupBy("property_number_of_reviews").count().orderBy("property_number_of_reviews").show()




+-------+------------------+
|summary|           ratings|
+-------+------------------+
|  count|           1528909|
|   mean| 4.359531103551759|
| stddev|1.3955799967422735|
|    min|                 0|
|    max|                 5|
+-------+------------------+

+-------+--------------------------+
|summary|property_number_of_reviews|
+-------+--------------------------+
|  count|                   1126797|
|   mean|         44.33635162322938|
| stddev|         73.02684481932725|
|    min|                         0|
|    max|                       997|
+-------+--------------------------+

+-------+------+
|ratings| count|
+-------+------+
|   NULL|     6|
|      0|133071|
|      1|  4063|
|   1.25|     1|
|   1.33|    16|
|   1.43|     1|
|    1.5|   144|
|   1.57|     1|
|    1.6|     1|
|   1.67|    30|
|   1.75|     7|
|    1.8|     1|
|   1.83|     1|
|      2|  2423|
|   2.14|     2|
|    2.2|     9|
|   2.25|    13|
|   2.29|     1|
|   2.33|   196|
|   2.38|     2|
+-------+----

#### Propery Rating & Reviews Score Calculation

In [0]:
from pyspark.sql.functions import when, col, log1p, lit

# Ratings Processing 

airbnb_df = airbnb_df.filter(
    col("ratings").isNotNull() & (col("ratings") != 0)
)
airbnb_df = airbnb_df.withColumn("ratings_int", col("ratings").cast("int")) 

rating_min = airbnb_df.agg({"ratings_int": "min"}).first()[0]
rating_max = airbnb_df.agg({"ratings_int": "max"}).first()[0]

airbnb_df = airbnb_df.withColumn( 
    "normalized_ratings",
    (col("ratings_int") - rating_min) / (rating_max - rating_min)
)

# Reviews Processing 

airbnb_df = airbnb_df.withColumn("property_number_of_reviews_int", col("property_number_of_reviews").cast("int")) 
median_reviews = airbnb_df.approxQuantile("property_number_of_reviews_int", [0.5], 0.01)[0]

airbnb_df = airbnb_df.withColumn(
    "property_number_of_reviews_int",
    when(
        col("property_number_of_reviews_int").isNull(), 
        lit(median_reviews)
    ).when(
        col("property_number_of_reviews_int") == 0,
        lit(median_reviews)
    ).otherwise(col("property_number_of_reviews_int"))
)

airbnb_df = airbnb_df.withColumn(
    "reviews_log",
    log1p(col("property_number_of_reviews_int")) 
)

reviews_min = airbnb_df.agg({"reviews_log": "min"}).first()[0]
reviews_max = airbnb_df.agg({"reviews_log": "max"}).first()[0]

airbnb_df = airbnb_df.withColumn(
    "normalized_reviews",
    (col("reviews_log") - reviews_min) / (reviews_max - reviews_min) 
)

airbnb_df = airbnb_df.withColumn(
    "z_rating",
    2 * col("normalized_ratings") - lit(1.0)
)

airbnb_df = airbnb_df.withColumn(
    "trust_factor",
    0.5 + 0.5 * col("normalized_reviews")
)

airbnb_df = airbnb_df.withColumn(
    "z_quality",
    col("z_rating") * col("trust_factor")
)

airbnb_df = airbnb_df.withColumn(
    "propery_rating_reviews_score",
    (col("z_quality") + lit(1.0)) / lit(2.0)
)


#### Host Ratings & Reviews Distribution Detection

In [0]:
# Distribution Detection 

airbnb_df.select("host_rating").describe().show()
airbnb_df.select("host_number_of_reviews").describe().show()

airbnb_df.groupBy("host_rating").count().orderBy("host_rating").show()
airbnb_df.groupBy("host_number_of_reviews").count().orderBy("host_number_of_reviews").show()


+-------+------------------+
|summary|       host_rating|
+-------+------------------+
|  count|           1391213|
|   mean| 4.707855367941619|
| stddev|0.6120564025037525|
|    min|                 0|
|    max|                 5|
+-------+------------------+

+-------+----------------------+
|summary|host_number_of_reviews|
+-------+----------------------+
|  count|               1391213|
|   mean|     922.6815944071828|
| stddev|    3714.4477067378657|
|    min|                     0|
|    max|                  9996|
+-------+----------------------+

+-----------+-----+
|host_rating|count|
+-----------+-----+
|       NULL| 4625|
|          0|18304|
|          1| 1556|
|       1.18|    2|
|       1.22|    1|
|       1.25|    3|
|       1.33|   13|
|        1.4|    4|
|       1.42|    1|
|       1.46|    1|
|       1.49|    1|
|        1.5|   62|
|       1.51|    4|
|       1.57|    3|
|        1.6|    9|
|       1.61|    1|
|       1.63|    2|
|       1.67|   21|
|       1.75|   15|


#### Host Rating & Reviews Score Calculation

In [0]:
from pyspark.sql.functions import when, col, log1p, lit 

# Host_Ratings Processing 

airbnb_df = airbnb_df.filter(
    col("host_rating").isNotNull() & (col("host_rating") != 0)
)
airbnb_df = airbnb_df.withColumn("host_rating_int", col("host_rating").cast("int")) 

rating_min = airbnb_df.agg({"host_rating_int": "min"}).first()[0] 
rating_max = airbnb_df.agg({"host_rating_int": "max"}).first()[0]

airbnb_df = airbnb_df.withColumn( 
    "normalized_host_rating",
    (col("host_rating_int") - rating_min) / (rating_max - rating_min)
)

# Host_Reviews Processing 

airbnb_df = airbnb_df.withColumn("host_number_of_reviews_int", col("host_number_of_reviews").cast("int")) 
median_reviews = airbnb_df.approxQuantile("host_number_of_reviews_int", [0.5], 0.01)[0]

airbnb_df = airbnb_df.withColumn(
    "host_number_of_reviews_int",
    when(
        col("host_number_of_reviews_int").isNull(), 
        lit(median_reviews)
    ).when(
        col("host_number_of_reviews_int") == 0,
        lit(median_reviews)
    ).otherwise(col("host_number_of_reviews_int")) 
)

airbnb_df = airbnb_df.withColumn(
    "host_reviews_log",
    log1p(col("host_number_of_reviews_int")) 
)

reviews_min = airbnb_df.agg({"host_reviews_log": "min"}).first()[0]
reviews_max = airbnb_df.agg({"host_reviews_log": "max"}).first()[0]

airbnb_df = airbnb_df.withColumn(
    "normalized_host_reviews",
    (col("host_reviews_log") - reviews_min) / (reviews_max - reviews_min)
)

airbnb_df = airbnb_df.withColumn(
    "z_host_rating",
    2 * col("normalized_host_rating") - lit(1.0) 
)

airbnb_df = airbnb_df.withColumn(
    "host_trust_factor",
    0.5 + 0.5 * col("normalized_host_reviews")
)

airbnb_df = airbnb_df.withColumn(
    "z_host_quality",
    col("z_host_rating") * col("host_trust_factor")
)

airbnb_df = airbnb_df.withColumn(
    "host_rating_reviews_score",
    (col("z_host_quality") + lit(1.0)) / lit(2.0)
)


#### Amenities Score Calculation

In [0]:
from pyspark.sql.types import ArrayType, StructType, StructField, StringType
from pyspark.sql.functions import (
    col,
    from_json,
    expr,
    array_contains,
    lit,
    greatest
)

# ============================================================
# 1. Define schema for the amenities JSON array
# ============================================================
amenities_schema = ArrayType(
    StructType([
        StructField("group_name", StringType()),
        StructField("items", ArrayType(
            StructType([
                StructField("name", StringType()),
                StructField("value", StringType())
            ])
        ))
    ])
)

# ============================================================
# 2. Parse the raw amenities JSON into a structured column
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "amenities_parsed",
    from_json(col("amenities"), amenities_schema)
)

# ============================================================
# 3. Extract all amenity values and names into flattened arrays
#     - amenity_values: machine-readable codes like SYSTEM_XXXX
#     - amenity_names: user-facing textual labels
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "amenity_values",
    expr("flatten(transform(amenities_parsed, g -> transform(g.items, i -> i.value)))")
)

airbnb_df = airbnb_df.withColumn(
    "amenity_names",
    expr("flatten(transform(amenities_parsed, g -> transform(g.items, i -> i.name)))")
)

# ============================================================
# 4. Heating / Cooling Features
#     We separate AC and Heating, then combine them into a
#     temperature comfort score (temp_score).
#     Logic:
#       - If either AC or Heating exists → base 2.5 points
#       - If BOTH exist → additional +0.5 points
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "has_ac",
    array_contains(col("amenity_values"), "SYSTEM_SNOWFLAKE").cast("int")
)

airbnb_df = airbnb_df.withColumn(
    "has_heating",
    array_contains(col("amenity_values"), "SYSTEM_THERMOMETER").cast("int")
)

airbnb_df = airbnb_df.withColumn(
    "temp_score",
    1.5 * greatest(col("has_ac"), col("has_heating")) +
    0.5 * ((col("has_ac") + col("has_heating") == 2).cast("int"))
)

# ============================================================
# 5. Internet / Connectivity Features
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "has_wifi",
    (
        array_contains(col("amenity_values"), "SYSTEM_WI_FI") |
        array_contains(col("amenity_values"), "SYSTEM_PORTABLE_WI_FI")
    ).cast("int")
)

# ============================================================
# 6. Parking Features
#     IMPORTANT: The value SYSTEM_MAPS_CAR_RENTAL appears for ALL
#     parking types. Therefore we MUST rely on the textual "name".
#
#     - Free parking:  "Free parking on premises", "Free street parking", etc.
#     - Paid parking:  "Paid parking on/off premises", "Paid parking lot", etc.
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "has_parking_free",
    expr("exists(amenity_names, n -> lower(n) LIKE '%free%park%')").cast("int")
)

airbnb_df = airbnb_df.withColumn(
    "has_parking_paid",
    expr("exists(amenity_names, n -> lower(n) LIKE '%paid%park%')").cast("int")
)

# ============================================================
# 7. Pool / Jacuzzi Features
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "has_pool",
    array_contains(col("amenity_values"), "SYSTEM_POOL").cast("int")
)

airbnb_df = airbnb_df.withColumn(
    "has_hot_tub",
    array_contains(col("amenity_values"), "SYSTEM_JACUZZI").cast("int")
)

# ============================================================
# 8. Family-Friendly Features
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "has_family",
    (
        array_contains(col("amenity_values"), "SYSTEM_CRIB") |
        array_contains(col("amenity_values"), "SYSTEM_PACK_N_PLAY") |
        array_contains(col("amenity_values"), "SYSTEM_HIGH_CHAIR") |
        array_contains(col("amenity_values"), "SYSTEM_TOYS") |
        array_contains(col("amenity_values"), "SYSTEM_BOARD_GAMES")
    ).cast("int")
)

# ============================================================
# 9. Nature Views (ocean, mountain, garden, beach)
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "has_nature_view",
    (
        array_contains(col("amenity_values"), "SYSTEM_VIEW_OCEAN") |
        array_contains(col("amenity_values"), "SYSTEM_VIEW_MOUNTAIN") |
        array_contains(col("amenity_values"), "SYSTEM_BEACH") |
        array_contains(col("amenity_values"), "SYSTEM_FLOWER")
    ).cast("int")
)

# ============================================================
# 10. City View
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "has_city_view",
    array_contains(col("amenity_values"), "SYSTEM_VIEW_CITY").cast("int")
)

# ============================================================
# 11. Kitchen Detection
#     We use name-based detection since not all kitchens have SYSTEM tags.
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "has_kitchen",
    (
        expr("exists(amenity_names, n -> n LIKE 'Kitchen%')") |
        expr("exists(amenity_names, n -> n LIKE 'Kitchenette%')")
    ).cast("int")
)

# ============================================================
# 12. Workspace
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "has_workspace",
    (
        array_contains(col("amenity_values"), "SYSTEM_WORKSPACE") |
        expr("exists(amenity_names, n -> lower(n) LIKE '%workspace%')")
    ).cast("int")
)

# ============================================================
# 13. Laundry Features (Washer / Dryer)
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "has_washer",
    array_contains(col("amenity_values"), "SYSTEM_WASHER").cast("int")
)

airbnb_df = airbnb_df.withColumn(
    "has_dryer",
    array_contains(col("amenity_values"), "SYSTEM_DRYER").cast("int")
)

# ============================================================
# 14. Final Amenities Score (Raw)
#
#     Combines all features with predefined weights.
#     temp_score already contributes up to 3.0 points.
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "amenities_score_raw",
    col("temp_score") +                     # Temperature comfort score (0–2.0)
    2 * col("has_wifi") +
    2.4 * col("has_parking_free") +         # Higher value than paid parking
    0.3 * col("has_parking_paid") +
    2.5 * col("has_pool") +
    1.5 * col("has_hot_tub") +
    1.2 * col("has_family") +
    1.8 * col("has_nature_view") +
    1.1 * col("has_city_view") +
    1.8 * col("has_kitchen") +
    0.9 * col("has_workspace") +
    0.7 * col("has_washer") +
    0.5 * col("has_dryer")
)

# ============================================================
# 15. Normalize Amenities Score to range [0, 1]
#     max_amenities_score = maximum theoretical score
# ============================================================
max_amenities_score = 18.7 # Sum of all weights

airbnb_df = airbnb_df.withColumn(
    "amenities_score",
    col("amenities_score_raw") / lit(max_amenities_score)
)


#### Cancellation Policy Score Calculation

In [0]:
from pyspark.sql.types import ArrayType, StructType, StructField, StringType
from pyspark.sql.functions import (
    col,
    from_json,
    expr,
    when,
    size,
    lit
)

# ============================================================
# 1. Define schema for cancellation_policy JSON
#     Each entry contains:
#       - cancellation_name  (e.g., "Full refund before…")
#       - cancellation_value (unused here but kept for completeness)
# ============================================================
cancellation_schema = ArrayType(
    StructType([
        StructField("cancellation_name", StringType()),
        StructField("cancellation_value", StringType())
    ])
) 

# ============================================================
# 2. Parse the cancellation_policy JSON string
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "cancellation_parsed",
    from_json(col("cancellation_policy"), cancellation_schema)
)

# ============================================================
# 3. Replace NULL with an empty array
#     This prevents errors when applying array operations
#     and defines a clear semantic:
#       NULL → treated as "no cancellation info provided"
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "cancellation_parsed",
    when(col("cancellation_parsed").isNull(), expr("array()"))
    .otherwise(col("cancellation_parsed"))
)

# ============================================================
# 4. Extract only the cancellation policy names
#     Example output:
#       ["Full refund before…", "Partial refund until…"]
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "cancellation_names",
    expr("transform(cancellation_parsed, c -> c.cancellation_name)")
)

# ============================================================
# 5. Detect refund types
#     We classify each listing into one of:
#       - full refund
#       - partial refund
#       - no refund
#
#     Important edge-case behavior:
#       - If there is *no* policy data → treat as "no refund"
# ============================================================

# -----------------------------
# Full refund detection
# -----------------------------
airbnb_df = airbnb_df.withColumn(
    "has_full_refund",
    when(
        size(col("cancellation_parsed")) == 0,        # No data → not full refund
        lit(False)
    ).otherwise(
        expr("exists(cancellation_names, n -> n LIKE 'Full refund%')")
    ).cast("int")
)

# -----------------------------
# Partial refund detection
# -----------------------------
airbnb_df = airbnb_df.withColumn(
    "has_partial_refund",
    when(
        size(col("cancellation_parsed")) == 0,        # No data → not partial refund
        lit(False)
    ).otherwise(
        expr("exists(cancellation_names, n -> n LIKE 'Partial refund%')")
    ).cast("int")
)

# -----------------------------
# No refund detection
#     Logic:
#       - If array is empty → assume no refund
#       - Else → check explicitly
# -----------------------------
airbnb_df = airbnb_df.withColumn(
    "has_no_refund",
    when(
        size(col("cancellation_parsed")) == 0,        # No data → assume no refund
        lit(True)
    ).otherwise(
        expr("exists(cancellation_names, n -> n LIKE 'No refund%')")
    ).cast("int")
)

# ============================================================
# 6. Construct cancellation_score
#
#     Score interpretation:
#       1.0 → full refund
#       0.5 → partial refund
#       0.0 → no refund
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "cancellation_score",
    when(col("has_full_refund") == 1, 1.0)
    .when(col("has_partial_refund") == 1, 0.5)
    .otherwise(0.0)
) 


#### Quality Score, Superhost Consideration and Final VFM Score

In [0]:
# ============================================================
# 1. Build quality_score based on your priority:
#    1) amenities_score
#    2) propery_rating_reviews_score
#    3) host_rating_reviews_score
#    4) cancellation_score
#
#    Weights sum to 1:
#      amenities_score              → 0.35
#      propery_rating_reviews_score → 0.35
#      host_rating_reviews_score    → 0.2
#      cancellation_score           → 0.1
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "quality_score",
    0.35 * col("amenities_score") +
    0.35 * col("propery_rating_reviews_score") + 
    0.2 * col("host_rating_reviews_score") +
    0.1 * col("cancellation_score")
)

# clip to [0, 1] if needed 
airbnb_df = airbnb_df.withColumn(
    "quality_score",
    when(col("quality_score") < 0, 0.0)
    .when(col("quality_score") > 1, 1.0)
    .otherwise(col("quality_score"))
)

# ============================================================
# 2. Superhost boost:
#    - is_supperhost is treated as 0/1
#    - We apply up to +10% boost for superhosts
# ============================================================
airbnb_df = airbnb_df.withColumn(
    "is_supperhost_int",
    when(
        (col("is_supperhost") == "TRUE"),
        lit(1)
    ).otherwise(lit(0))
)

superhost_boost = 0.10  # 10% bonus

airbnb_df = airbnb_df.withColumn(
    "superhost_factor",
    1.0 + superhost_boost * col("is_supperhost_int") 
)

# ============================================================
# 10. Final Value for Money Index
#
#     value_for_money_index_raw =
#         quality_score * sqrt(price_score) * superhost_factor 
#
#     Then clamp to [0, 1] for interpretability.
# ============================================================
price_alpha = 0.5  # weakening price influence

airbnb_df = airbnb_df.withColumn(
    "value_for_money_raw",
    col("quality_score") *
    F.pow(col("price_score"), price_alpha) *
    col("superhost_factor")
)

# Clip to [0, 1] for interpretability
airbnb_df = airbnb_df.withColumn(
    "value_for_money",
    F.when(col("value_for_money_raw") < 0, F.lit(0.0))
     .when(col("value_for_money_raw") > 1, F.lit(1.0))
     .otherwise(col("value_for_money_raw"))
)


display(airbnb_df)

name price image description category availability discount reviews ratings seller_info breadcrumbs location lat long guests pets_allowed description_items category_rating house_rules details highlights arrangement_details amenities images available_dates url final_url listing_title property_id listing_name location_details description_by_sections description_html location_details_html is_supperhost host_number_of_reviews host_rating hosts_year host_response_rate is_guest_favorite travel_details pricing_details total_price currency cancellation_policy property_number_of_reviews country postcode_map_url host_image host_details guests_int guests_safe price_per_guest price_per_guest_clipped price_per_guest_norm price_score ratings_int normalized_ratings property_number_of_reviews_int reviews_log normalized_reviews z_rating trust_factor z_quality propery_rating_reviews_score host_rating_int normalized_host_rating host_number_of_reviews_int host_reviews_log normalized_host_reviews z_host_rating host_trust_factor z_host_quality host_rating_reviews_score amenities_parsed amenity_values amenity_names has_ac has_heating temp_score has_wifi has_parking_free has_parking_paid has_pool has_hot_tub has_family has_nature_view has_city_view has_kitchen has_workspace has_washer has_dryer amenities_score_raw amenities_score cancellation_parsed cancellation_names has_full_refund has_partial_refund has_no_refund cancellation_score quality_score is_supperhost_int superhost_factor value_for_money_raw value_for_money Rental unit in Broadbeach · ★4.96 · 2 bedrooms · 2 beds · 1 bath 238 https://a0.muscache.com/pictures/50ddeaed-5302-4d0c-8200-163b2cddd071.jpg Our exceptionally stylish two bedroom, one bathroom LUXURY holiday apartment is located in the ORACLE T2, right in the heart of beautiful Broadbeach! Every corner of this gorgeous apartment overflows with style, luxury and thoughtful touches. Relax on the ocean facing balcony located directly above the manicured garden terrace and take in the relaxing views and sea breezes. This property is all class and guaranteed to satisfy even the fussiest Airbnb guest!The spaceThe photos speak for themselves. They are a true, accurate and up to date representation of our immaculately presented, squeaky clean, apartment. The furnishings are practical and comfortable and the linen and bedding are soft and luxurious. The master king bedroom opens out onto the large balcony. The second bedroom is a small internal room with a comfortable high quality queen sized bed. The second bedroom does not have a window. Each bedroom has an internal sliding door which provides access to the two way bathroom. Our apartment has been styled with a relaxing holiday in mind.Guest accessPoolSpaGymSauna and steam roomBBQ and entertaining areasGardensSecure off street parking for ONE vehicleAccess to facilities is not guaranteed and may be interrupted by routine and unexpected maintenance schedules.Other things to noteThis property accommodates up to FOUR people only. Children aged two and older are included in the four people rule. No exceptions. Infants UNDER the age of two are very welcome at our place and may stay at no additional charge however we do not provide linen or bedding. Let us know if you would like the link to a local business who hires out baby equipment (travel cots, strollers, high chairs).CHECK IN Available between 3pm and 9pm.Self check in is NOT available at this property. After hours check ins are NOT available. A 3pm check in is not guaranteed and depends on cleaning schedules. CHECK IN APPOINTMENTOur lovely host welcomes you in person on arrival. The booking guest is required to make contact with us via the booking message thread prior to their arrival day to arrange a check in time. A host will not be onsite to meet you unless you have scheduled a check in time. We always do our best to fit in with your travel schedule. IMPORTANTKeys and security fobs will only be issued to the person who made the booking. 

### Proximity Score Logic & User Workflow

In [0]:
%python
from pyspark.sql import functions as F
from pyspark.sql import Window
from pyspark.sql.types import ArrayType, StringType
import json
import os
from IPython.display import display, HTML

# ==============================================================================
# part 1: Spark Backend - Data Preparation
# ==============================================================================

# 1. Preparing hotel data
ab_cols = airbnb_df.columns
lat_c = "lat" if "lat" in ab_cols else "latitude"
lon_c = "long" if "long" in ab_cols else "longitude"
name_c = "name" if "name" in ab_cols else "property_id"
url_c = "url" if "url" in ab_cols else "final_url"

airbnb_ready = airbnb_df.select(
    F.col("property_id"),
    F.split(F.split(F.split(F.col(name_c), "·").getItem(0), "★").getItem(0), "\|").getItem(0).alias("name"),
    F.col(lat_c).alias("latitude"),
    F.col(lon_c).alias("longitude"),
    F.col("price_per_guest"),
    F.col("guests_safe"),
    F.col("value_for_money"),
    F.col("ratings").alias("rating"),
    F.col("available_dates"),
    F.col(url_c).alias("original_link")
)

# 2. Preparing the games
matches_all = matches_df.select(
    F.col("match_id"),
    F.col("home_team"),
    F.col("away_team"),
    F.col("stadium_name"),
    F.col("Country").alias("match_country"),
    (F.col("City") if "City" in matches_df.columns else F.col("Country")).alias("match_city"),
    F.col("Date").alias("match_date_raw"),
    F.col("latitude").alias("match_lat"),
    F.col("longitude").alias("match_lon")
).withColumn("match_date", F.to_date("match_date_raw"))

# 3. Join
joined_df = airbnb_ready.crossJoin(F.broadcast(matches_all))

# 4. Calculating distance
R = 6371.0
lat1, lon1 = F.radians(joined_df.latitude), F.radians(joined_df.longitude)
lat2, lon2 = F.radians(joined_df.match_lat), F.radians(joined_df.match_lon)
dlat, dlon = lat2 - lat1, lon2 - lon1
a = F.pow(F.sin(dlat/2), 2) + F.cos(lat1) * F.cos(lat2) * F.pow(F.sin(dlon / 2), 2)
c = 2 * F.asin(F.sqrt(a))
joined_df = joined_df.withColumn("distance_km", R * c)

# 5. Filter out non-nearby locations
candidates_df = joined_df.filter(F.col("distance_km") <= 50)

# Availability filter
candidates_df = candidates_df.withColumn(
    "all_dates_arr", 
    F.from_json(F.col("available_dates"), ArrayType(StringType()))
)

candidates_df = candidates_df.withColumn("min_check", F.date_sub("match_date", 5).cast("string"))
candidates_df = candidates_df.withColumn("max_check", F.date_add("match_date", 5).cast("string"))

candidates_df = candidates_df.withColumn(
    "relevant_dates", 
    F.expr("filter(all_dates_arr, x -> x >= min_check AND x <= max_check)")
)

candidates_df = candidates_df.filter(
    F.array_contains(F.col("relevant_dates"), F.col("match_date").cast("string"))
)

candidates_df = candidates_df.drop("available_dates", "all_dates_arr", "min_check", "max_check")


# 6. Score
W_PROX, W_VFM = 0.6, 0.4 
candidates_df = candidates_df.withColumn(
    "proximity_score", 
    F.pow(F.greatest(F.lit(0), F.lit(1) - (F.col("distance_km") / 50)), 1.8)
).withColumn(
    "final_score", 
    (W_PROX * F.col("proximity_score")) + (W_VFM * F.col("value_for_money"))
)

# 7. Top 100
window_spec = Window.partitionBy("match_id").orderBy(
    F.col("final_score").desc(), 
    F.col("property_id").asc()
)
top_candidates = candidates_df.withColumn("rank", F.rank().over(window_spec)) \
    .filter(F.col("rank") <= 100)

# 8. Data Packaging
results_rows = top_candidates.collect()
recommendations_map = {}

for row in results_rows:
    m_id = str(row['match_id'])
    if m_id not in recommendations_map: recommendations_map[m_id] = []
    
    avail_list = row['relevant_dates'] if row['relevant_dates'] else []

    recommendations_map[m_id].append({
        "id": str(row['property_id']),
        "name": row['name'].strip(),
        "link": row['original_link'],
        "price": float(row['price_per_guest'] or 0), 
        "rating": float(row['rating'] or 0),
        "distance": float(row['distance_km']),
        "score": float(row['final_score']),
        "guests": int(row['guests_safe'] or 2),
        "vfm": float(row['value_for_money'] or 0),
        "prox": float(row['proximity_score'] or 0),
        "availability": avail_list,
        # --- NEW: Map Coordinates ---
        "lat": float(row['latitude']),
        "lon": float(row['longitude'])
    })

matches_data_js = []
for row in matches_all.collect():
    d = row.asDict()
    location_str = d['match_country']
    if d['match_city'] and d['match_city'].lower() != d['match_country'].lower():
        location_str = d['match_country'] 

    matches_data_js.append({
        "id": str(d['match_id']),
        "home": d['home_team'],
        "away": d['away_team'],
        "host": d['home_team'],
        "stadium": d['stadium_name'],
        "location": location_str,
        "date": str(d['match_date']),
        # --- NEW: Stadium Coordinates ---
        "lat": float(d['match_lat']),
        "lon": float(d['match_lon'])
    })

matches_json = json.dumps(matches_data_js)
recommendations_json = json.dumps(recommendations_map)
teams_json = json.dumps(sorted(list(set([m['home'] for m in matches_data_js] + [m['away'] for m in matches_data_js]))))


### Validation

In [0]:
from pyspark.sql import functions as F


# 1. Filter for the Top 30 ranked listings only and cast rating to double
# We select listings with rank <= 30 to focus on the highest-priority recommendations.
df_top_30 = top_candidates.filter(F.col("rank") <= 30) \
    .withColumn("rating_num", F.col("rating").cast("double"))

# 2. Generate binary flags based on validation criteria (1 = Pass, 0 = Fail)
# Criteria defined: Distance < 15 km AND Rating >= 4.0
df_checked = df_top_30.withColumn(
    "pass_dist", 
    F.when(F.col("distance_km") < 15.0, 1).otherwise(0)
).withColumn(
    "pass_rate", 
    F.when(F.col("rating_num") >= 4.0, 1).otherwise(0)
).withColumn(
    "pass_both", 
    F.when((F.col("distance_km") < 15.0) & (F.col("rating_num") >= 4.0), 1).otherwise(0)
)

# 3. Calculate success metrics per match
# Group by match_id to compute the percentage of listings meeting criteria for each game.
match_stats = df_checked.groupBy("match_id").agg(
    F.avg("pass_dist").alias("pct_dist"),
    F.avg("pass_rate").alias("pct_rate"),
    F.avg("pass_both").alias("pct_both")
)

# 4. Calculate global averages
# Aggregating the per-match statistics to get a single performance score for the entire dataset.
final_results = match_stats.select(
    F.avg("pct_dist").alias("avg_dist"),
    F.avg("pct_rate").alias("avg_rate"),
    F.avg("pct_both").alias("avg_both")
).collect()

# 5. Display the final results
print("-" * 60)
if final_results:
    row = final_results[0]
    # Convert decimal fractions to percentages
    res_dist = (row['avg_dist'] or 0) * 100
    res_rate = (row['avg_rate'] or 0) * 100
    res_both = (row['avg_both'] or 0) * 100

    print(f"🏆 Validation Results (Top 30 Only):")
    print("-" * 60)
    print(f"✅ Distance (< 15 km):       {res_dist:.2f}% of listings")
    print(f"✅ Quality (>= 4.0):        {res_rate:.2f}% of listings")
    print(f"🌟 Perfect Match (Both):    {res_both:.2f}% of listings")
    print("-" * 60)
else:
    print("⚠️ No data found (Table is empty or calculation failed).")

------------------------------------------------------------
🏆 Validation Results (Top 30 Only):
------------------------------------------------------------
✅ Distance (< 15 km):       78.21% of listings
✅ Quality (>= 4.0):        97.52% of listings
🌟 Perfect Match (Both):    76.54% of listings
------------------------------------------------------------


### The Final Interface

In [0]:
# ==============================================================================
# Part 2: HTML
# ==============================================================================

html_code = f"""
<!DOCTYPE html>
<html>
<head>
<meta charset="utf-8">
<title>MatchPoint - Match & Hotel Search Engine</title>
<link rel="stylesheet" href="https://unpkg.com/leaflet@1.9.4/dist/leaflet.css" />
<script src="https://unpkg.com/leaflet@1.9.4/dist/leaflet.js"></script>
<script src="https://cdn.jsdelivr.net/npm/canvas-confetti@1.6.0/dist/confetti.browser.min.js"></script>

<style>
    body {{ font-family: 'Segoe UI', sans-serif; background: #f0f2f5; color: #333; margin: 0; padding: 20px; }}
    .container {{ max-width: 950px; margin: 0 auto; }}
    .card {{ background: white; border-radius: 12px; box-shadow: 0 2px 10px rgba(0,0,0,0.1); padding: 25px; margin-bottom: 20px; }}
    h1 {{ text-align: center; color: #1877f2; }}
    h3 {{ margin-top: 0; color: #444; border-bottom: 1px solid #eee; padding-bottom: 10px; }}
    
    /* Map Styles */
    #map {{
        height: 400px;
        width: 100%;
        border-radius: 12px;
        margin-bottom: 25px; 
        border: 2px solid #eee;
        z-index: 1;
    }}

    .form-row {{ display: flex; gap: 15px; flex-wrap: wrap; align-items: flex-end; }}
    .form-group {{ flex: 1; min-width: 150px; }}
    label {{ display: block; margin-bottom: 6px; font-weight: 600; font-size: 0.9em; color: #555; }}
    input, select {{ width: 100%; padding: 10px; border: 1px solid #ccc; border-radius: 8px; font-size: 1em; box-sizing: border-box; }}
    
    button {{ cursor: pointer; transition: 0.2s; }}
    .btn-primary {{ background: #1877f2; color: white; border: none; padding: 10px 25px; border-radius: 8px; font-size: 1em; }}
    .btn-primary:hover {{ background: #1461c7; }}
    
    .btn-action {{ 
        display: block; 
        width: 100%;    
        padding: 10px 0; 
        border-radius: 5px; 
        margin-top: 8px; 
        text-align: center;
        text-decoration: none; 
        font-size: 1em; 
        font-weight: bold;
        border: none;
        box-sizing: border-box; 
        cursor: pointer;
        transition: 0.2s;
    }}
    
    .btn-green {{ background: #2ecc71; color: white; }}
    .btn-green:hover {{ background: #27ae60; }}
    
    .btn-blue {{ background: #3498db; color: white; }}
    .btn-blue:hover {{ background: #2980b9; }}
    
    .btn-purple {{ background: #9b59b6; color: white; }}
    .btn-purple:hover {{ background: #8e44ad; }}

    table {{ width: 100%; border-collapse: collapse; margin-top: 10px; }}
    th, td {{ padding: 12px; text-align: left; border-bottom: 1px solid #eee; }}
    th {{ background: #f8f9fa; }}
    tr:hover {{ background: #f1f2f6; }}
    
    th:first-child, td:first-child {{ white-space: nowrap; min-width: 120px; }}
    
    .hotel-card {{ display: flex; border: 1px solid #e1e4e8; border-radius: 10px; overflow: hidden; margin-bottom: 15px; background: white; }}
    .hotel-left {{ background: #f8f9fa; width: 60px; display: flex; flex-direction: column; align-items: center; justify-content: center; border-right: 1px solid #eee; padding: 5px; text-align: center; }}
    .score-circle {{ width: 50px; height: 50px; background: #2ecc71; color: white; border-radius: 50%; display: flex; align-items: center; justify-content: center; font-weight: bold; margin-bottom: 5px; }}
    .rank-text {{ font-size: 0.8em; color: #777; }}
    
    .hotel-info {{ padding: 20px; flex: 1; }}
    .hotel-right {{ padding: 20px; background: #fafbfc; border-left: 1px solid #eee; display: flex; flex-direction: column; justify-content: center; min-width: 180px; }}
    
    .badge {{ display: inline-block; padding: 3px 8px; border-radius: 4px; font-size: 0.75em; margin-right: 5px; }}
    .bg-blue {{ background: #e3f2fd; color: #1565c0; }}
    .bg-orange {{ background: #fff3e0; color: #ef6c00; }}
    
    .hidden {{ display: none !important; }}
    
    option:disabled {{ color: #aaa; background-color: #f0f0f0; font-style: italic; }}
    
    .error-msg {{
        background-color: #fff3cd;
        color: #856404;
        padding: 15px;
        border-radius: 8px;
        border: 1px solid #ffeeba;
        text-align: center;
        font-weight: bold;
        margin-top: 20px;
    }}

    .modal-overlay {{
        position: fixed;
        top: 0; left: 0; width: 100%; height: 100%;
        background: rgba(0, 0, 0, 0.6);
        display: flex;
        align-items: center;
        justify-content: center;
        z-index: 2000;
        backdrop-filter: blur(4px);
    }}
    .modal-content {{
        background: white;
        padding: 40px;
        border-radius: 20px;
        text-align: center;
        max-width: 450px;
        width: 90%;
        box-shadow: 0 15px 40px rgba(0,0,0,0.3);
        animation: popIn 0.3s ease-out;
    }}
    @keyframes popIn {{
        0% {{ transform: scale(0.8); opacity: 0; }}
        100% {{ transform: scale(1); opacity: 1; }}
    }}
    .success-icon {{
        font-size: 70px;
        color: #2ecc71;
        margin-bottom: 20px;
    }}
    .booking-details {{
        background: #f8f9fa;
        padding: 20px;
        border-radius: 12px;
        margin: 20px 0;
        text-align: left;
        border: 1px solid #eee;
    }}
    .booking-row {{ display: flex; justify-content: space-between; margin-bottom: 10px; font-size: 1.1em; }}
    .booking-label {{ font-weight: bold; color: #555; }}
    .booking-val {{ font-weight: bold; color: #333; }}
    
    /* Stadium Guide Modal Styles */
    .guide-modal-content {{
        background: white;
        padding: 30px;
        border-radius: 20px;
        max-width: 600px;
        width: 90%;
        max-height: 80vh;
        overflow-y: auto;
        box-shadow: 0 15px 40px rgba(0,0,0,0.3);
        animation: popIn 0.3s ease-out;
        text-align: left;
    }}
    .guide-header {{
        display: flex;
        justify-content: space-between;
        align-items: center;
        border-bottom: 2px solid #9b59b6;
        padding-bottom: 15px;
        margin-bottom: 20px;
    }}
    .guide-title {{
        color: #9b59b6;
        margin: 0;
        font-size: 1.5em;
    }}
    .close-btn {{
        background: none;
        border: none;
        font-size: 1.5em;
        cursor: pointer;
        color: #999;
    }}
    .close-btn:hover {{ color: #333; }}
    .guide-body {{
        line-height: 1.8;
    }}
    .guide-body strong {{
        color: #333;
    }}
    .stadium-info-btn {{
        background: none;
        border: 1px solid #9b59b6;
        color: #9b59b6;
        padding: 3px 10px;
        border-radius: 5px;
        cursor: pointer;
        font-size: 0.85em;
        margin-left: 10px;
    }}
    .stadium-info-btn:hover {{
        background: #9b59b6;
        color: white;
    }}
</style>
</head>
<body>

<div class="container">
    <h1>⚽ MatchPoint</h1>

    <div class="card" id="step1">
        <h3>Select a Match</h3>
        <div class="form-row">
            <div class="form-group"><label>Team</label><input list="teams" id="teamInput" placeholder="Search team...">
            <datalist id="teams"></datalist></div>
            <div class="form-group"><label>From Date</label><input type="date" id="dateFrom"></div>
            <div class="form-group"><label>To Date</label><input type="date" id="dateTo"></div>
            <div class="form-group" style="flex:0;"><button class="btn-primary" onclick="searchMatches()">Search</button></div>
        </div>
        <div id="matchesResults"></div>
    </div>

    <div class="card hidden" id="step2" style="border-top: 4px solid #f39c12;">
        <h3>Details: <span id="selectedMatchTitle" style="color:#f39c12"></span></h3>
        <p style="font-size:0.9em; color:#666;">
            Match Date: <span id="matchDateDisplay"></span> | 
            Stadium: <span id="matchStadiumDisplay"></span>
            <button class="stadium-info-btn" onclick="showStadiumGuide(currentStadium)">📍 Stadium Info</button>
        </p>
        <div class="form-row">
            <div class="form-group"><label>👥 Guests</label><input type="number" id="inputGuests" value="2" min="1"></div>
            <div class="form-group"><label>🌙 Nights</label><input type="number" id="inputNights" value="3" min="1"></div>
            <div class="form-group"><label>💰 Budget per person (€)</label><input type="number" id="inputBudget" value="200"></div>
            <div class="form-group" style="flex:0;"><button class="btn-primary" style="background:#f39c12;" onclick="findHotels()">Show Hotels</button></div>
        </div>
    </div>

    <div class="card hidden" id="step3" style="border-top: 4px solid #2ecc71;">
        <h3>Recommended Hotels</h3>
        <div id="map"></div>
        <div id="hotelsList"></div>
    </div>
</div>

<div id="bookingModal" class="modal-overlay hidden">
    <div class="modal-content">
        <div class="success-icon">🎉</div>
        <h2 style="margin-top:0; color:#2ecc71;">Booking Confirmed!</h2>
        <p style="color:#666; margin-bottom:20px;">Thank you for choosing MatchPoint. Your booking has been received.</p>
        
        <div class="booking-details">
            <div class="booking-row">
                <span class="booking-label">Total:</span>
                <span class="booking-val" id="modalPrice"></span>
            </div>
            <div class="booking-row">
                <span class="booking-label">Hotel:</span>
                <span class="booking-val" id="modalHotel"></span>
            </div>
            <div class="booking-row">
                <span class="booking-label">Dates:</span>
                <span class="booking-val" id="modalDateInfo"></span>
            </div>
        </div>
        
        <p style="font-size:0.9em; color:#888; margin-bottom:20px;">Confirmation sent to your email 📧</p>
        <button class="btn-primary" style="width:100%; font-size:1.1em;" onclick="closeModal()">Close & Search More</button>
    </div>
</div>

<div id="guideModal" class="modal-overlay hidden">
    <div class="guide-modal-content">
        <div class="guide-header">
            <h2 class="guide-title" id="guideStadiumName">🏟️ Stadium Guide</h2>
            <button class="close-btn" onclick="closeGuideModal()">✕</button>
        </div>
        <div class="guide-body" id="guideContent">
            Loading...
        </div>
        <button class="btn-primary btn-purple" style="width:100%; margin-top:20px;" onclick="closeGuideModal()">Close</button>
    </div>
</div>

<script>
    const allMatches = {matches_json};
    const allRecs = {recommendations_json};
    const teams = {teams_json};
    const stadiumGuides = {stadium_guides_json};
    
    let currentMatchId = null;
    let currentMatchDate = null;
    let currentStadium = null;
    let map = null;

    const dl = document.getElementById('teams');
    teams.forEach(t => {{ let op = document.createElement('option'); op.value = t; dl.appendChild(op); }});

    // --- MAP FUNCTIONALITY ---
    function initMap(match, hotels) {{
        if (map) {{ map.remove(); }}
        
        map = L.map('map').setView([match.lat, match.lon], 13);
        
        L.tileLayer('https://{{s}}.tile.openstreetmap.org/{{z}}/{{x}}/{{y}}.png', {{
            attribution: '© OpenStreetMap contributors'
        }}).addTo(map);

        // Soccer Ball Icon for Stadium
        var stadiumIcon = L.icon({{
            iconUrl: 'https://cdn-icons-png.flaticon.com/512/53/53283.png', 
            iconSize: [40, 40],
            iconAnchor: [20, 40],
            popupAnchor: [0, -40]
        }});

        L.marker([match.lat, match.lon], {{icon: stadiumIcon}})
         .addTo(map)
         .bindPopup("<b>🏟️ " + match.stadium + "</b><br>Match Location")
         .openPopup();

        var bounds = L.latLngBounds();
        bounds.extend([match.lat, match.lon]);

        hotels.forEach((h, index) => {{
            var hotelMarker = L.marker([h.lat, h.lon]).addTo(map);
            hotelMarker.bindPopup(
                "<b>" + h.name + "</b><br>" +
                "Price: €" + h.price.toFixed(0) + "<br>" +
                "Rating: ⭐" + h.rating.toFixed(1) + "<br>" +
                "Distance: " + h.distance.toFixed(1) + " km<br>" + 
                "Score: " + (h.score * 100).toFixed(0) + "%"
            );
            bounds.extend([h.lat, h.lon]);
        }});

        map.fitBounds(bounds, {{padding: [50, 50]}});
    }}

    // Convert markdown-style formatting to HTML
    function formatGuide(text) {{
        if (!text) return 'No guide available';
        return text
            .replace(/\\*\\*(.+?)\\*\\*/g, '<strong>$1</strong>')
            .replace(/\\* /g, '• ')
            .replace(/\\n/g, '<br>');
    }}

    function showStadiumGuide(stadiumName) {{
        const guide = stadiumGuides[stadiumName];
        const modal = document.getElementById('guideModal');
        const titleEl = document.getElementById('guideStadiumName');
        const contentEl = document.getElementById('guideContent');
        
        if (guide) {{
            titleEl.innerText = '🏟️ ' + guide.stadium + ' (' + guide.team + ')';
            contentEl.innerHTML = formatGuide(guide.guide);
        }} else {{
            titleEl.innerText = '🏟️ ' + stadiumName;
            contentEl.innerHTML = 'No guide available for this stadium.';
        }}
        
        modal.classList.remove('hidden');
    }}

    function closeGuideModal() {{
        document.getElementById('guideModal').classList.add('hidden');
    }}

    function searchMatches() {{
        const teamVal = document.getElementById('teamInput').value.toLowerCase();
        const dFrom = document.getElementById('dateFrom').value;
        const dTo = document.getElementById('dateTo').value;

        const res = allMatches.filter(m => {{
            const tm = (!teamVal || m.home.toLowerCase().includes(teamVal) || m.away.toLowerCase().includes(teamVal));
            const dt = (!dFrom || m.date >= dFrom) && (!dTo || m.date <= dTo);
            return tm && dt;
        }});

        const div = document.getElementById('matchesResults');
        if(res.length === 0) {{ div.innerHTML = '<p>No matches found.</p>'; return; }}
        
        let html = '<table><thead><tr><th>Date</th><th>Match</th><th>Stadium</th><th>Location</th><th></th></tr></thead><tbody>';
        res.forEach(m => {{
            const hasGuide = stadiumGuides[m.stadium] ? '📍' : '';
            html += '<tr>' +
                '<td>' + m.date + '</td>' +
                '<td><strong>' + m.home + '</strong> vs <strong>' + m.away + '</strong></td>' +
                '<td>' + m.stadium + ' ' + hasGuide + '</td>' +
                '<td>' + m.location + '</td>' +
                '<td><button class="btn-primary" style="padding:5px 15px; font-size:0.9em;" onclick="selectMatch(\\'' + m.id + '\\', \\'' + m.home + ' vs ' + m.away + '\\', \\'' + m.date + '\\', \\'' + m.stadium.replace(/'/g, "\\\\'") + '\\')">Select</button></td>' +
            '</tr>';
        }});
        div.innerHTML = html + '</tbody></table>';
        document.getElementById('step2').classList.add('hidden');
        document.getElementById('step3').classList.add('hidden');
    }}

    function selectMatch(id, title, date, stadium) {{
        currentMatchId = id;
        currentMatchDate = new Date(date);
        currentStadium = stadium;
        document.getElementById('selectedMatchTitle').innerText = title;
        document.getElementById('matchDateDisplay').innerText = date;
        document.getElementById('matchStadiumDisplay').innerText = stadium;
        document.getElementById('step2').classList.remove('hidden');
        document.getElementById('step3').classList.add('hidden');
        document.getElementById('step2').scrollIntoView({{behavior:'smooth'}});
    }}

    function generateDateOptionsHTML(matchDate, nights, availableDatesList) {{
        const availableSet = new Set(availableDatesList);
        let html = '<select style="margin-top:5px; background:#f9f9f9; width:100%;">';
        
        let hasAtLeastOneOption = false;

        for (let i = 0; i < nights; i++) {{
            let start = new Date(matchDate);
            start.setDate(start.getDate() - (nights - 1) + i);
            
            let end = new Date(start);
            end.setDate(end.getDate() + nights);
            
            let fmt = d => d.toISOString().split('T')[0];
            let startStr = fmt(start);
            let endStr = fmt(end);
            
            let isAvailable = true;
            let checkDate = new Date(start);
            for(let d = 0; d < nights; d++) {{
                let dateString = fmt(checkDate);
                if (!availableSet.has(dateString)) {{
                    isAvailable = false;
                    break;
                }}
                checkDate.setDate(checkDate.getDate() + 1);
            }}
            
            if (isAvailable) hasAtLeastOneOption = true;

            let disabledAttr = isAvailable ? '' : 'disabled';
            let label = startStr + ' → ' + endStr + (isAvailable ? '' : ' (Unavailable)');
            let val = startStr + ' → ' + endStr;
            html += '<option ' + disabledAttr + ' value="' + val + '">' + label + '</option>';
        }}
        
        html += '</select>';
        return {{ html: html, hasAvailability: hasAtLeastOneOption }};
    }}

    function showError(msg) {{
        const listDiv = document.getElementById('hotelsList');
        listDiv.innerHTML = '<div class="error-msg">⚠️ ' + msg + '</div>';
        document.getElementById('step3').classList.remove('hidden');
        document.getElementById('step3').scrollIntoView({{behavior:'smooth'}});
    }}

    function openModal(name, price, index) {{
        let selectBox = document.getElementById('dateSelect' + index);
        let selectedDate = selectBox ? selectBox.value : "No date selected";
        
        document.getElementById('modalHotel').innerText = name;
        document.getElementById('modalPrice').innerText = price;
        document.getElementById('modalDateInfo').innerText = selectedDate;
        
        document.getElementById('bookingModal').classList.remove('hidden');

        if (typeof confetti === 'function') {{
            var duration = 3000;
            var end = Date.now() + duration;

            (function frame() {{
                confetti({{
                    particleCount: 5,
                    angle: 60,
                    spread: 55,
                    origin: {{ x: 0 }},
                    zIndex: 9999
                }});
                confetti({{
                    particleCount: 5,
                    angle: 120,
                    spread: 55,
                    origin: {{ x: 1 }},
                    zIndex: 9999
                }});

                if (Date.now() < end) {{
                    requestAnimationFrame(frame);
                }}
            }}());
        }}
    }}

    function closeModal() {{
        document.getElementById('bookingModal').classList.add('hidden');
    }}

    function findHotels() {{
        if(!currentMatchId) return;
        
        let guestsVal = document.getElementById('inputGuests').value;
        let nightsVal = document.getElementById('inputNights').value;
        let budgetVal = document.getElementById('inputBudget').value;
        
        let guests = guestsVal ? parseInt(guestsVal) : 1;
        let nights = nightsVal ? parseInt(nightsVal) : 1;
        let budget = budgetVal ? parseFloat(budgetVal) : 999999;
        
        const budgetFlex = budget + 20.0;

        const candidates = allRecs[currentMatchId] || [];

        if (candidates.length === 0) {{ showError("No hotels available near the stadium for this match date."); return; }}
        const budgetCandidates = candidates.filter(h => h.price <= budgetFlex);
        if (budgetCandidates.length === 0) {{ showError("No hotels found within your budget."); return; }}
        const nightsCandidates = budgetCandidates.filter(h => {{
            const check = generateDateOptionsHTML(currentMatchDate, nights, h.availability);
            return check.hasAvailability;
        }});
        if (nightsCandidates.length === 0) {{ showError("No hotels available for " + nights + " consecutive nights around the match date."); return; }}
        const finalCandidates = nightsCandidates.filter(h => h.guests >= guests);
        if (finalCandidates.length === 0) {{ showError("No hotels found for " + guests + " guests."); return; }}

        finalCandidates.sort((a,b) => b.score - a.score);
        const top10 = finalCandidates.slice(0, 10);

        // --- MAP INIT ---
        const matchData = allMatches.find(m => m.id === currentMatchId);
        document.getElementById('step3').classList.remove('hidden');
        setTimeout(() => {{
            initMap(matchData, top10);
        }}, 100);

        const listDiv = document.getElementById('hotelsList');
        listDiv.innerHTML = '';

        top10.forEach((h, i) => {{
            let isOverBudget = h.price > budget;
            let priceColor = isOverBudget ? '#e67e22' : '#27ae60';
            let extraTag = isOverBudget ? '<span class="badge bg-orange">Over Budget</span>' : '';
            
            let pricePerNightDisplay = h.price.toFixed(2);
            let totalVal = h.price * nights * guests;
            let totalPriceDisplay = "€" + totalVal.toLocaleString('en-US', {{minimumFractionDigits: 2, maximumFractionDigits: 2}});

            let vfm = (h.vfm * 100).toFixed(1);
            let finalScore = (h.score * 100).toFixed(1);

            let dateResult = generateDateOptionsHTML(currentMatchDate, nights, h.availability);
            let selectHTML = dateResult.html.replace('<select', '<select id="dateSelect' + i + '"');
            let safeName = h.name.replace(/'/g, "\\'");
            let airbnbLink = h.link ? h.link : 'https://www.airbnb.com/rooms/' + h.id;

            listDiv.innerHTML += 
            '<div class="hotel-card">' +
                '<div class="hotel-left">' +
                    '<div class="score-circle">' + finalScore + '%</div>' +
                    '<div class="rank-text">Match</div>' +
                    '<div class="rank-text" style="font-weight:bold; margin-top:5px;">#' + (i+1) + '</div>' +
                '</div>' +
                '<div class="hotel-info">' +
                    '<h3 style="margin:0;">' + h.name + (isOverBudget ? ' 💎' : '') + '</h3>' +
                    '<p style="margin:5px 0; color:#666;">📍 ' + h.distance.toFixed(1) + ' km | ⭐ ' + h.rating.toFixed(1) + '</p>' +
                    '<div><span class="badge bg-blue">VFM: ' + vfm + '%</span> ' + extraTag + '</div>' +
                    '<div style="margin-top:10px; font-size:0.9em;">' +
                        '<label style="margin-right:5px;">Select dates:</label>' +
                        selectHTML +
                    '</div>' +
                '</div>' +
                '<div class="hotel-right">' +
                    '<div style="font-size:1.6em; font-weight:bold; color:' + priceColor + ';">€' + pricePerNightDisplay + '</div>' +
                    '<div style="font-size:0.8em; color:#777;">per person/night</div>' +
                    '<div style="font-size:0.85em; color:#333; margin-top:5px; font-weight:bold; background:#eee; padding:3px; border-radius:4px; text-align:center;">' +
                        'Total: ' + totalPriceDisplay +
                    '</div>' +
                    '<div style="margin-top:10px;">' +
                        '<button class="btn-action btn-green" onclick="openModal(\\'' + safeName + '\\', \\'' + totalPriceDisplay + '\\', ' + i + ')">Book</button>' +
                        '<a href="' + airbnbLink + '" target="_blank" class="btn-action btn-blue">View</a>' +
                    '</div>' +
                '</div>' +
            '</div>';
        }});
        
        document.getElementById('step3').scrollIntoView({{behavior:'smooth'}});
    }}

    // Close modals on escape key
    document.addEventListener('keydown', function(e) {{
        if (e.key === 'Escape') {{
            closeModal();
            closeGuideModal();
        }}
    }});
</script>

</body>
</html>
"""

# ==============================================================================
# Save HTML file
# ==============================================================================
import os

file_name = "MatchPoint_App.html"
save_path = f"/dbfs/FileStore/{file_name}"

with open(save_path, "w", encoding='utf-8') as f:
    f.write(html_code)

print(f"✅ HTML file saved successfully!")

from IPython.display import display, HTML

download_link = f"""
<div style="text-align:center; margin-top:20px; padding:20px; background:#e3f2fd; border-radius:10px; border:1px solid #1877f2;">
    <h2 style="color:#1877f2;">🎉 Application Ready!</h2>
    <p>Click the button below to open the app in a new tab:</p>
    <a href="/files/{file_name}" target="_blank" style="background:#1877f2; color:white; padding:15px 30px; text-decoration:none; border-radius:8px; font-weight:bold; font-size:1.2em;">
        Open MatchPoint 🚀
    </a>
</div>
"""

display(HTML(download_link))

✅ HTML file saved successfully!
